In [1]:
import importcsv

print('Importing csv file...........')
small_dataset = importcsv.opencsv('processedspeech.csv')  

Importing csv file...........


In [2]:
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf_vectorizer = TfidfVectorizer(min_df=0.001)
tfidf_matrix = tfidf_vectorizer.fit_transform(small_dataset['processed_speeches'])

num of comp = 30 => 30 groups of speeches?

No, `n_components` is the number of concepts we want to reduce our matrix to.

In [3]:
from sklearn.decomposition import TruncatedSVD

# it takes about 3 minutes for 500 components
svd = TruncatedSVD(n_components=1000) 

U = svd.fit_transform(tfidf_matrix)
S = svd.singular_values_
V = svd.components_

In [8]:
import pickle

def saveUSV(U, S, V, filename):
    pack = [U, S, V]
    with open(filename, 'wb') as fo:
        pickle.dump(pack, fo)

def loadUSV(filename):
    with open(filename, 'rb') as fo:
        r = pickle.load(fo)
        U, S, V = r[0], r[1], r[2]
        return U,S,V
filename = 'USV.pkl'
# saveUSV(U,S,V, filename) 
# U,S,V = loadUSV(filename)

In [4]:
print(V)
print('S', S)

[[ 1.32797983e-03  5.91210276e-04  6.18608755e-04 ...  1.54210769e-03
   7.37955717e-04  7.76371351e-04]
 [-6.03834424e-04 -1.23816070e-04 -2.65345718e-04 ... -8.44222559e-04
  -5.40960436e-04 -6.65232254e-04]
 [-5.93215880e-05  3.94417353e-04  2.56577658e-04 ... -5.42561975e-04
   5.30119824e-05 -3.57881918e-04]
 ...
 [ 2.88246172e-03  3.31730028e-04 -2.26530713e-04 ... -1.10788658e-03
   1.09500376e-03  2.27732383e-04]
 [-8.10356625e-04 -5.49416295e-04 -3.30374877e-04 ... -6.32126657e-04
   1.86674056e-03 -1.94201538e-04]
 [ 1.90910309e-03  3.50145647e-04 -5.58942345e-04 ...  1.69102001e-04
  -1.47771311e-03 -4.29605292e-04]]
S [124.7694159   59.70213408  51.88242396  49.90511528  41.1485064
  39.69715821  35.534353    34.70651034  33.66151611  33.10387845
  32.0052946   31.32628592  30.61204948  29.73994903  29.72896001
  29.04100894  28.5905262   27.94408406  27.17744625  26.66462101
  26.20927101  25.81972178  25.42136875  25.35915299  24.81575375
  24.6565023   24.25747921  24.00

In [24]:
# Αυτός ο κώδικας τυπώνει τις λέξεις-κλειδιά ανά θεματική περιοχή που εντοπίστηκε
# Δηλαδή για το concept 0 οι λέξεις κλειδιά που το περιγράφουν είναι οι 
# κυρι, υπουργ, υπαρχ, κυβερνης, πολιτικ ....
feature_names = tfidf_vectorizer.get_feature_names_out()
top_keywords_per_concept = 5
for i in range(500): # for all n_components
    top_indices = np.argsort(V[i])[::-1][:top_keywords_per_concept]

    top_keywords = [feature_names[index] for index in top_indices]

    print(f'Top keywords for concept i: {i}: {top_keywords}')

Top keywords for Dimension i: 0: ['κυρι', 'υπουργ', 'υπαρχ', 'κυβερνης', 'πολιτικ']
Top keywords for Dimension i: 1: ['βουλ', 'συνεδριας', 'θεωρει', 'καλωσοριζ', 'μαθητ']
Top keywords for Dimension i: 2: ['ερωτης', 'επικαιρ', 'αριθμ', 'βουλευτ', 'υπουργ']
Top keywords for Dimension i: 3: ['αρθρ', 'τροπολογι', 'νομοσχεδι', 'δεκτ', 'συζητης']
Top keywords for Dimension i: 4: ['αρθρ', 'δεκτ', 'υπουργει', 'σχεδι', 'συνολ']
Top keywords for Dimension i: 5: ['νοσοκομει', 'υγει', 'υπαρχ', 'τροπολογι', 'εργ']
Top keywords for Dimension i: 6: ['τροπολογι', 'ευρω', 'αγροτ', 'αγροτικ', 'τραπεζ']
Top keywords for Dimension i: 7: ['υγει', 'νοσοκομει', 'γιατρ', 'τροπολογι', 'νομοσχεδι']
Top keywords for Dimension i: 8: ['αρθρ', 'παραγραφ', 'εργαζομεν', 'υγει', 'ασφαλιστικ']
Top keywords for Dimension i: 9: ['τροπολογι', 'αρθρ', 'εκπαιδευτικ', 'πολιτικ', 'εκπαιδευς']
Top keywords for Dimension i: 10: ['τροπολογι', 'βουλευτ', 'κατεθες', 'κοινοβουλευτικ', 'εργ']
Top keywords for Dimension i: 11: ['αγρο

In [27]:
# Let's try to find the most important keywords for each document
# Ο Παπαδοπουλος μηδενίζει τα r-k σ του διαγώνιου πίνακα S και παίρνει μόνο τα k σημαντικότερα
# Εδώ δεν μηδενίζω τίποτα, απλά τυπώνω τα 10 πρώτα σημαντικότερα keywords
# Μάλλον θα πρέπει να κάνουμε κι έναν καθαρισμό στις λέξεις που έχουμε, να μην κρατάμε όσες έχουν πχ ψηφία μέσα?
top_concepts_per_document = 10

for i in range(len(A)):
    top_indices = np.argsort(U[i])[::-1][:top_concepts_per_document]
    
    top_keywords = [feature_names[index] for index in top_indices]

    print(f'Top concepts per document {i}: {top_keywords}')

Top concepts per document 0: ['01', '000', 'αγγλικ', 'ad', 'αγανακτης', '10', '1100', 'αγρι', 'αγωνιζοντα', '60']
Top concepts per document 1: ['28000000000', '105', '107', '250', '000', '106', '2190', '112', '300000', '1967']
Top concepts per document 2: ['112', '000', '106', '01', '107', '10', '114', '10ετια', '100000', '131']
Top concepts per document 3: ['01', '10', '000', '112', '136', '133', '2006', '3000000', '15', '105']
Top concepts per document 4: ['112', '01', '000', '105', '10', '28000000000', '10ετια', '114', '106', '08']
Top concepts per document 5: ['000', '10', '2022', '117', '87', '106', 'of', '112', '109', '1989']
Top concepts per document 6: ['105', '7000', '106', 'αδιαφορ', 'αδιεξοδ', '107', '28000000000', '112', '000', '1960']
Top concepts per document 7: ['112', '1700', '114', '106', '105', 'internet', '33', '10', '235', '1920']
Top concepts per document 8: ['000', '01', '28', '08', '280', '116', '26', '26ησ', '100000', '330']
Top concepts per document 9: ['01', '

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Top concepts per document 138512: ['15', '154', '10000000000', '126', '118', '150000', '127', '12000', '16', '1500']
Top concepts per document 138513: ['000', '15', '154', '14', '10000000000', '126', '127', '16', '1100', '160']
Top concepts per document 138514: ['000', '15', '154', '1100', '14', '127', '1500', '150000', '156', '160']
Top concepts per document 138515: ['000', '15', '154', '1100', '10000000000', '150000', '110', '1600', '126', '127']
Top concepts per document 138516: ['000', '15', '154', '127', 'αδει', '126', '16', '150000', 'αδιαφανει', '12000']
Top concepts per document 138517: ['000', '120', '13', 'αγροφυλακ', '1100', '123', '129', 'αγν', '1981', 'αγορ']
Top concepts per document 138518: ['000', '10000000000', '03', '05', '2003', '08', '138', '1977', '121', '1955']
Top concepts per document 138519: ['000', '2006', '1977', '1984', '46', '2001', '1985', '400', '1987', 'off']
Top concepts per document 138520: ['000', '2005', '30', '245', '48', '2018', '300', '39', '113',

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Top concepts per document 271167: ['000', '06', '100000000', '165', '180', '1980', '138', '19', '210', 'αγοραστ']
Top concepts per document 271168: ['000', '06', '1981', '125', '200000', '118', '180', '1987', '05', '1975']
Top concepts per document 271169: ['000', '1985', '1981', '118', '1950', '06', '1975', '1ο', '39', '155']
Top concepts per document 271170: ['000', '10000000000', '1990', '08', '2005', '250', '1996', '2030', '24', '20000']
Top concepts per document 271171: ['000', '38', '1980', '63', '500000000', '450', '180', '400000000', '21ου', '46']
Top concepts per document 271172: ['01', '000', '04', '119', '12', '05', '10000000', '127', '125', 'αγωνιωδ']
Top concepts per document 271173: ['000', '1973', '100000000', '10ετια', '165', '148', '19', '102', '1951', '153']
Top concepts per document 271174: ['000', '1951', '100000000', '155', '1000000', '10ετια', '13', '2007', '1100', '1995']
Top concepts per document 271175: ['000', '102', '10ετια', '77', '165', '1973', '155', '1984

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Top concepts per document 359225: ['000', '154', '1100', '12000', '15', '04', '150000', '10000000000', '126', '1500']
Top concepts per document 359226: ['000', '06', '113', '110', '1600', '1982', '100000', '2018', '109', '154']
Top concepts per document 359227: ['000', 'αγγιξ', '18', '06', 'ecu', 'email', '08', 'funds', 'αδιαφαν', 'αδιακριτ']
Top concepts per document 359228: ['101', '1000000000', '000', '185', '01', '10000000000', '1000', '175', '102', '110']
Top concepts per document 359229: ['000', '154', '10000000000', '15', '126', '14', '04', '12000', '156', '1500']
Top concepts per document 359230: ['000', '2004', '10000000000', 'offshore', '1821', 'αγελαδ', '2000', '200000', '125', '35']
Top concepts per document 359231: ['000', '06', '101', '141', '1500', '133', '109', '1976', '100000000', '10']
Top concepts per document 359232: ['1500', '000', '148', '141', '10', '185', '101', '150000', '160', '20']
Top concepts per document 359233: ['000', '104', '101', 'αδρ', '1821', '154', 

In [4]:
# V30 = V[:30,:]

# keep only the first 50 values of S, the rest must be 0
S50 = [v if idx < 50 else 0 for idx, v in enumerate(S)] 

In [5]:
import numpy as np

# M = np.dot(tfidf_matrix, V30.transpose())
A = np.dot(U, S50)

## Let's try to keep the most important concepts
We'll keep 80% of the concepts

In [7]:
total_energy = sum(e*e for e in S)
# we want 80% of the initial energy
goal = 0.8 * total_energy

# Then keep summing elements of S until you've reached the goal energy! Simple
# This way, the number of concepts we'll keep is automatically calculated

Sk = np.zeros_like(S) # make an empty array of size like S
energy = 0 # keep track of energy, until we've reached the goal
for i, e in enumerate(S): # could this be done with list comprehension? 
    # irrelevant, wouldn't really save much time, for 500-1000 iterations anyway
    Sk[i] = e
    energy += e ** 2
    if energy > goal:
        print(f'Stopping at iteration {i} and value of e: {e}')
        break

Sk

Stopping at iteration 554 and value of e: 10.30249588655432


array([124.7694159 ,  59.70213408,  51.88242396,  49.90511528,
        41.1485064 ,  39.69715821,  35.534353  ,  34.70651034,
        33.66151611,  33.10387845,  32.0052946 ,  31.32628592,
        30.61204948,  29.73994903,  29.72896001,  29.04100894,
        28.5905262 ,  27.94408407,  27.17744626,  26.66462102,
        26.20927103,  25.81972183,  25.4213688 ,  25.35915305,
        24.81575383,  24.6565024 ,  24.25747936,  24.00568821,
        23.74504941,  23.56189278,  23.26611173,  22.95700771,
        22.63591051,  22.56541173,  22.47630253,  22.33053994,
        22.18612475,  21.92920782,  21.8351794 ,  21.67188581,
        21.4675602 ,  21.32083771,  21.28097702,  21.1810047 ,
        20.98661726,  20.79511465,  20.70289174,  20.66110451,
        20.61345628,  20.48600971,  20.34530136,  20.26252496,
        20.16940451,  20.08172666,  19.96694455,  19.87097604,
        19.73302301,  19.70129067,  19.6805772 ,  19.54706066,
        19.30497407,  19.27592715,  19.26851858,  19.11